# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by Coursera/IBM

## Table of Contents

* [Introduction](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction/Business Problem <a name="introduction"></a>

### Description and Discussion of the Background

Munich is the capital and most populous city of Bavaria.
With a population of around 1.5 million it is the third-largest city in Germany, according to
[Wikipedia](https://en.wikipedia.org/wiki/Munich).  
There is the website
[www.moving-to-munich.com](https://www.moving-to-munich.com)
which lists the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/):

* Altstadt
* Au
* Bogenhausen
* Giesing (Ober- and Untergiesing)
* Haidhausen
* Isarvorstadt
* Lehel
* Neuhausen
* Schwabing
* Thalkirchen

These are roughly 10 of a total of 25 districts in Munich.
Although the website describes the individual neighborhoods, it does not give precise reasons for the selection of these districts compared to the rest.

The idea of this project is to check if someone can make a similar selection based on the venues in each district.
In addition, it might be possible to find neighborhoods that may have similar characteristics.
These candidates would potentially have a comparable lifestyle, but probably lower rents.
If you want to move to Munich then this information might be of interest for you.


### Initialization of Python Environment

Install and import all needed libraries:

In [1]:
#!conda install -c conda-forge folium=0.5.0 --yes
#!conda install -c conda-forge geopy --yes
#!conda install -c conda-forge geocoder --yes
#!conda install -c conda-forge gdal --yes
#!conda install -c conda-forge selenium --yes

import pandas as pd
import numpy as np

from bs4 import BeautifulSoup
import requests
import io
import os
import time
import urllib.request
from pathlib import Path

import json
import math

import folium
from folium.features import DivIcon
import geocoder
from osgeo import ogr
from selenium import webdriver
from selenium.webdriver.firefox.firefox_binary import FirefoxBinary

from sklearn.cluster import KMeans

%matplotlib inline
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt

import sys
print(sys.version)

3.7.6 | packaged by conda-forge | (default, Jan  7 2020, 22:33:48) 
[GCC 7.3.0]


## Data <a name="data"></a>

The investigation is based on the following sources:

* Based on the website
[www.moving-to-munich.com](https://www.moving-to-munich.com)
a list of the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
([https://www.moving-to-munich.com/best-neighborhoods-in-munich/](https://www.moving-to-munich.com/best-neighborhoods-in-munich/))
is created and modified by hand to represent the _official_ names of Munich's boroughs.
* All 25 _official_ names of Munich's boroughs are retrieved from a
[Wikipedia](https://de.wikipedia.org/wiki/Stadtbezirke_M%C3%BCnchens)
([https://de.wikipedia.org/wiki/Stadtbezirke_M%C3%BCnchens](https://de.wikipedia.org/wiki/Stadtbezirke_M%C3%BCnchens))
page.
* For visualisation purpose the borders of Munich's boroughs are obtained from the website
[www.arcgis.com](https://www.arcgis.com).  
It provides the _vector geometries_ of
[Munich Districts and Subdistricts for free download and use](https://www.arcgis.com/home/item.html?id=369c18dfc10d457d9d1afb28adcc537b).
By using 
[mapshaper.org](https://mapshaper.org/)
the data is transformed into a suitable
[GeoJSON file format](https://en.wikipedia.org/wiki/GeoJSON).
The border of each borough is stored as a polygon which is used to determine each borough's center and extent.
* The venue data of Munich's boroughs is retrieved by using
[Foursquare](https://foursquare.com).
Several radii are used for obtaining some kind of robust venue list for each borough.
The lists of venues for all boroughs are used and a _k-means_ clustering method is applied to group similar neighborhoods. 
 
The above steps should make it possible to identify neighborhoods with a similar lifestyle like the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/).


### Best Neighborhoods in Munich
According to the website
[www.moving-to-munich.com](https://www.moving-to-munich.com)
the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
would be:

* Altstadt
* Au
* Bogenhausen
* Giesing (Ober- and Untergiesing)
* Haidhausen
* Isarvorstadt
* Lehel
* Neuhausen
* Schwabing
* Thalkirchen

The _official_ names of the boroughs are a little bit different.
We create a list of the _best_ boroughs using the _official_ names:
```
   Best Neighborhoods:                    Official Borough Names: 
   * Altstadt                         -->   Altstadt-Lehel
   * Au                               -->   Au-Haidhausen
   * Bogenhausen                       =    Bogenhausen
   * Giesing (Ober- and Untergiesing) -->   Obergiesing-Fasangarten
                                      -->   Untergiesing-Harlaching
   * Haidhausen                       -->   Au-Haidhausen (see above)
   * Isarvorstadt                     -->   Ludwigsvorstadt-Isarvorstadt
   * Lehel                            -->   Altstadt-Lehel (see above)
   * Neuhausen                        -->   Neuhausen-Nymphenburg
   * Schwabing                        -->   Schwabing-West
                                      -->   Schwabing-Freimann
   * Thalkirchen                      -->   Thalkirchen-Obersendling-Forstenried-Fürstenried-Solln
```


In [2]:
# List of best Neighborhoods of Munich:
bestBoroughs = ['Altstadt-Lehel',
                'Au-Haidhausen',
                'Bogenhausen',
                'Obergiesing-Fasangarten',
                'Untergiesing-Harlaching',
                'Ludwigsvorstadt-Isarvorstadt',
                'Neuhausen-Nymphenburg',
                'Schwabing-West',
                'Schwabing-Freimann',
                'Thalkirchen-Obersendling-Forstenried-Fürstenried-Solln']

### Retrieve Boroughs of Munich

Obtain the _official_ names of Munich's boroughs from
[Wikipedia.org](https://de.wikipedia.org/wiki/Stadtbezirke_M%C3%BCnchens)
and store the data in a file locally: 

In [3]:
# scrape data from wikipedia to get the boroughs of munich
url = "https://de.wikipedia.org/wiki/Stadtbezirke_M%C3%BCnchens"
fnMunichWikiRawCSV = "Munich_25_WikiRaw.csv"

# save (cache) the data locally:
if not Path(fnMunichWikiRawCSV).is_file():
    with requests.get(url, timeout=5) as response:
        soup = BeautifulSoup(response.content, 'html.parser')
        table = soup.find("table", class_="wikitable sortable")

        # extract header:
        header = table.tbody.find_all("tr")[0]
        heading = []
        for th in header.find_all("th"):
            # remove any newlines and strip
            heading.append(th.text.strip())

        # extract rows:
        rows = []
        table_rows = table.find_all('tr')
        for tr in table_rows:
            td = tr.find_all('td')
            rows.append([i.text.strip() for i in td])
        rows = rows[1:]

        dfMunich = pd.DataFrame(rows, columns=heading)
        dfMunich.to_csv(fnMunichWikiRawCSV, index = False)
        print("File " + fnMunichWikiRawCSV + " saved.")
else:
    print("File " + fnMunichWikiRawCSV + " already exists locally.")

File Munich_25_WikiRaw.csv already exists locally.


Wrangle the data, i.e. assign english column names, set the data types correctly and assign an index:

In [4]:
# load the locally stored data:
dfMunich = pd.read_csv(fnMunichWikiRawCSV, dtype=str)

# remove last row (as it is a kind of summary row):
dfMunich = dfMunich[:-1]

# rename column names:
dfMunich.rename(columns={'Nr.': 'Id',
                         'Stadtbezirk': 'Borough', 
                         'Fläche(km²)': 'Area(km**2)',
                         'Einwohner': 'Residents',
                         'Dichte(Einw./km²)': 'Density(resident/km**2)',
                         'Ausländer(%)': 'Foreigners(%)'
                        }, inplace=True)

# change datatypes, cast numeric data:  
dfMunich = dfMunich.astype({'Id':np.int64})
dfMunich['Area(km**2)'            ] = pd.to_numeric(dfMunich['Area(km**2)'            ].astype(str).str.replace(',','.'))
dfMunich['Residents'              ] = pd.to_numeric(dfMunich['Residents'              ].astype(str).str.replace('.','' ))
dfMunich['Density(resident/km**2)'] = pd.to_numeric(dfMunich['Density(resident/km**2)'].astype(str).str.replace('.','' ))
dfMunich['Foreigners(%)'          ] = pd.to_numeric(dfMunich['Foreigners(%)'          ].astype(str).str.replace(',','.'))

# assign index:
dfMunich.set_index('Id', inplace=True)

# incorporate the `bestBoroughs` into Munich's borough dataframe:
dfBestBorough = pd.DataFrame({'Borough' : bestBoroughs, 'bestBorough' : 1})
dfMunich = dfMunich.merge(dfBestBorough, on='Borough', how="outer")
dfMunich.fillna(0, inplace=True)
dfMunich = dfMunich.astype({'bestBorough':np.int64})

print(dfMunich.shape)
print(dfMunich.dtypes)
dfMunich

(25, 6)
Borough                     object
Area(km**2)                float64
Residents                    int64
Density(resident/km**2)      int64
Foreigners(%)              float64
bestBorough                  int64
dtype: object


Borough  Area(km**2)  Residents  \
0                                      Altstadt-Lehel         3.15      21100   
1                        Ludwigsvorstadt-Isarvorstadt         4.40      51644   
2                                         Maxvorstadt         4.30      51402   
3                                      Schwabing-West         4.36      68527   
4                                       Au-Haidhausen         4.22      61356   
5                                            Sendling         3.94      40983   
6                                   Sendling-Westpark         7.81      59643   
7                                    Schwanthalerhöhe         2.07      29743   
8                               Neuhausen-Nymphenburg        12.91      98814   
9                                             Moosach        11.09      54223   
10                              Milbertshofen-Am Hart        13.42      75094   
11                                 Schwabing-Freimann        25.67      77936   
12                                        Bogenhausen        23.71      87950   
13                                       Berg am Laim         6.31      46098   
14                                     Trudering-Riem        22.45      73206   
15                                 Ramersdorf-Perlach        19.90     116327   
16                            Obergiesing-Fasangarten         5.72      54256   
17                            Untergiesing-Harlaching         8.06      53184   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...        17.76      96714   
19                                             Hadern         9.22      49898   
20                                 Pasing-Obermenzing        16.50      74625   
21                         Aubing-Lochhausen-Langwied        34.06      47813   
22                                Allach-Untermenzing        15.45      33355   
23                             Feldmoching-Hasenbergl        28.94      61774   
24                                               Laim         5.29      56546   

    Density(resident/km**2)  Foreigners(%)  bestBorough  
0                      6708           26.1            1  
1                     11734           28.4            1  
2                     11960           25.4            0  
3                     15706           22.7            1  
4                     14541           23.5            1  
5                     10405           26.9            0  
6                      7632           28.9            0  
7                     14367           33.5            0  
8                      7651           24.3            1  
9                      4888           31.5            0  
10                     5597           40.8            0  
11                     3036           29.3            1  
12                     3709           24.4            1  
13                     7300           31.9            0  
14                     3261           23.3            0  
15                     5847           33.9            0  
16                     9485           31.1            1  
17                     6601           24.1            1  
18                     5445           27.4            1  
19                     5410           27.3            0  
20                     4523           22.9            0  
21                     1404           28.4            0  
22                     2159           24.2            0  
23                     2135           32.4            0  
24                    10698           28.5            0

### Retrieve Borders of Munich's Boroughs

For visualisation purpose the borders of Munich's boroughs are required.
The following procedure was applied to obtain a _GeoJSON_ file describing these borders. 

1. The website
[www.arcgis.com](https://www.arcgis.com)
provides the _vector geometries_ of
[Munich Districts and Subdistricts for free download and use](https://www.arcgis.com/home/item.html?id=369c18dfc10d457d9d1afb28adcc537b).

2. The downloaded file _Munich_districts25_subdistricts105.lpk_ is a [7-zip](https://www.7-zip.org/) archive which contains (beside ohters) the following files:
```
    commondata/data0/Munich_25_Bezirke_Dissolved.dbf
    commondata/data0/Munich_25_Bezirke_Dissolved.prj
    commondata/data0/Munich_25_Bezirke_Dissolved.shp
    commondata/data0/Munich_25_Bezirke_Dissolved.shx
```

3. These files were uploaded to
[https://mapshaper.org/](https://mapshaper.org/)
using the options _detect line intersections_ and _snap vertices_.

4. By exporting the data from [https://mapshaper.org/](https://mapshaper.org/) the file _Munich_25_Bezirke_Dissolved.json_ is obtained.

5. There are two minor errors which are corrected by hand and saved again in file _Munich_25_Bezirke_Dissolved.json_ :
```
    "Tudering-Riem" --> "Trudering-Riem"
    "Obergiesing"   --> "Obergiesing-Fasangarten"
```

### Center and Extent of Munich's Boroughs
When analysing the file _Munich_25_Bezirke_Dissolved.json_, it turns out that the geometry of the boroughs is described by one polygon for each borough.  
For each polygon we will calculate its centroid (`coord_lat`, `coord_lng`) and an estimation of an radius (`radius(m)`) which describes roughly the extent of each borough:

In [5]:
def distanceOnEarth(lng1, lat1, lng2, lat2):
    # use https://en.wikipedia.org/wiki/Haversine_formula / https://en.wikipedia.org/wiki/Great-circle_distance to calc the "distance"
    dLat = abs(lat2 - lat1) * math.pi/180.0
    dLng = abs(lng2 - lng1) * math.pi/180.0
    a = (math.sin(dLat/2.0))**2 + math.cos(lat1*math.pi/180.0)*math.cos(lat2*math.pi/180.0)*(math.sin(dLng/2.0))**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    return 6371 * 1000 * c       

fnTownGeo = 'Munich_25_Bezirke_Dissolved.json' # geojson file

with open(fnTownGeo) as jsonFile:
    townGeo= json.load(jsonFile)    
    for feature in townGeo['features']:
        g = ogr.CreateGeometryFromJson(json.dumps(feature['geometry']))
        centroid = g.Centroid()
        dfMunich.loc[dfMunich['Borough'] == feature['properties']['FIRST_Bezi'], 'coord_lat'] = centroid.GetY()
        dfMunich.loc[dfMunich['Borough'] == feature['properties']['FIRST_Bezi'], 'coord_lng'] = centroid.GetX()
        radius = 0
        for pt in g.GetGeometryRef(0).GetPoints():
            radius = max(radius, distanceOnEarth(pt[0], pt[1], centroid.GetX(), centroid.GetY()))
        dfMunich.loc[dfMunich['Borough'] == feature['properties']['FIRST_Bezi'], 'radius(m)'] = round(radius,1)
        
    # calculate coordinates of whole Munich for centering the view:
    cMunichLat = dfMunich['coord_lat'].mean()+0.01
    cMunichLng = dfMunich['coord_lng'].mean()        

dfMunich

Borough  Area(km**2)  Residents  \
0                                      Altstadt-Lehel         3.15      21100   
1                        Ludwigsvorstadt-Isarvorstadt         4.40      51644   
2                                         Maxvorstadt         4.30      51402   
3                                      Schwabing-West         4.36      68527   
4                                       Au-Haidhausen         4.22      61356   
5                                            Sendling         3.94      40983   
6                                   Sendling-Westpark         7.81      59643   
7                                    Schwanthalerhöhe         2.07      29743   
8                               Neuhausen-Nymphenburg        12.91      98814   
9                                             Moosach        11.09      54223   
10                              Milbertshofen-Am Hart        13.42      75094   
11                                 Schwabing-Freimann        25.67      77936   
12                                        Bogenhausen        23.71      87950   
13                                       Berg am Laim         6.31      46098   
14                                     Trudering-Riem        22.45      73206   
15                                 Ramersdorf-Perlach        19.90     116327   
16                            Obergiesing-Fasangarten         5.72      54256   
17                            Untergiesing-Harlaching         8.06      53184   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...        17.76      96714   
19                                             Hadern         9.22      49898   
20                                 Pasing-Obermenzing        16.50      74625   
21                         Aubing-Lochhausen-Langwied        34.06      47813   
22                                Allach-Untermenzing        15.45      33355   
23                             Feldmoching-Hasenbergl        28.94      61774   
24                                               Laim         5.29      56546   

    Density(resident/km**2)  Foreigners(%)  bestBorough  coord_lat  coord_lng  \
0                      6708           26.1            1  48.141273  11.583178   
1                     11734           28.4            1  48.130152  11.561218   
2                     11960           25.4            0  48.148069  11.564298   
3                     15706           22.7            1  48.166539  11.569307   
4                     14541           23.5            1  48.129727  11.594758   
5                     10405           26.9            0  48.115282  11.546057   
6                      7632           28.9            0  48.116790  11.520021   
7                     14367           33.5            0  48.136161  11.538246   
8                      7651           24.3            1  48.156452  11.519305   
9                      4888           31.5            0  48.181714  11.510923   
10                     5597           40.8            0  48.195994  11.567868   
11                     3036           29.3            1  48.192805  11.610558   
12                     3709           24.4            1  48.157458  11.643526   
13                     7300           31.9            0  48.126164  11.631715   
14                     3261           23.3            0  48.123764  11.683573   
15                     5847           33.9            0  48.099738  11.638702   
16                     9485           31.1            1  48.102744  11.593269   
17                     6601           24.1            1  48.098586  11.564134   
18                     5445           27.4            1  48.086525  11.513238   
19                     5410           27.3            0  48.113956  11.483451   
20                     4523           22.9            0  48.152697  11.463274   
21                     1404           28.4            0  48.164726  11.408340   
22                     2159           24.2            0  48.192671  11.46200

Retrieve the polygons of the best boroughs and store it in `bestBoroughsPolygons`:

In [6]:
bestBoroughsPolygons = []
with open(fnTownGeo) as jsonFile:
    townGeo= json.load(jsonFile)    
    for feature in townGeo['features']:
        if (feature['properties']['FIRST_Bezi'] in bestBoroughs):
            aPolygon = []
            for pt in feature['geometry']['coordinates'][0]:
                aPolygon.append([pt[1],pt[0]])
            bestBoroughsPolygons.append(aPolygon)
#bestBoroughsPolygons

Let's visualize the 
[Best Neighborhoods](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
(red filled polygons with cyan borders) on a map of Munich:

In [7]:
# create town map
town_map = folium.Map(location=[cMunichLat, cMunichLng], zoom_start=12)#, tiles='Mapbox Bright')

# add boroughs to map:
town_map.choropleth(
    geo_data=fnTownGeo,
    data=dfMunich,
    columns=['Borough', 'bestBorough'],
    key_on='feature.properties.FIRST_Bezi',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=1.0,
    #legend_name='Best Boroughs',
    reset=True
    )

# remove legend:
for key in town_map._children:
    if key.startswith('color_map'):
        del(town_map._children[key])
        
# town_map, add polylines to show "bestBoroughs"
for polygon in bestBoroughsPolygons:
    folium.PolyLine(polygon, color="cyan", weight=4, opacity=1).add_to(town_map)

town_map        

Define a function to save screenshots of the Folium maps:

In [8]:
def saveMap(filenameNr, aMap):
    fnHTML='Munich_25_town_map_{}.html'.format(filenameNr)
    fnPNG ='Munich_25_town_map_{}.png'.format(filenameNr)
    tmpurl='file://{path}/{mapfile}'.format(path=os.getcwd(), mapfile=fnHTML)
    
    if not Path(fnPNG).is_file():
        aMap.save(fnHTML)
        binary = FirefoxBinary('/usr/bin/firefox')
        browser = webdriver.Firefox(firefox_binary=binary)
        browser.get(tmpurl)
        time.sleep(5)
        browser.save_screenshot(fnPNG)
        browser.quit()
    else:
        print("File " + fnPNG + " already exists locally.")

In [9]:
saveMap('01', town_map)

File Munich_25_town_map_01.png already exists locally.


To get an impression what the data looks like, here is a map which shows the _centroids_ (black dots) and the _extent_ (red circles) of each borough.
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
are drawn as red filled polygons with cyan borders.

In [10]:
# town_map, add radii to map = rough estimation of the extent of each borough
for lat, lng, radius in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['radius(m)']):
    folium.Circle(
        [lat, lng],
        radius=radius,
        color='red',
        fill=False,
        parse_html=False).add_to(town_map)

# town_map, add markers = centroid of each borough
for lat, lng, label in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['Borough']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.4,
        parse_html=False).add_to(town_map)     

print("min(radius(m))={}m, max(radius(m))={}m".format(dfMunich['radius(m)'].min(),dfMunich['radius(m)'].max()))

town_map

min(radius(m))=1190.7m, max(radius(m))=4974.5m


The picture shows each borough with its own extent as a circle of influence.
The radii vary between 1191m and 4975m.
Therefore it is important in further investigations to consider the radius of the respective borough. 

In [11]:
saveMap('02', town_map)

File Munich_25_town_map_02.png already exists locally.


### Retrieve venue data of Munich's boroughs using [Foursquare](https://foursquare.com)

Loading my [Foursquare](https://foursquare.com) credentials from separate file:

In [12]:
import MyCredentials  # MyCredentials.py stores the info to keep my credentials hidden
FOURSQUARE_CLIENT_ID = MyCredentials.FOURSQUARE_CLIENT_ID # your Foursquare ID
FOURSQUARE_CLIENT_SECRET = MyCredentials.FOURSQUARE_CLIENT_SECRET # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 200 # limit of number of venues returned by Foursquare API

Define a function to retrieve a list of venues _nearby_ to a certain location (`latitudes`, `longitudes`).  
For each coordinate, the results of the individual venues are limited to the specified distance (`radii`) to the given location.  
Before each [Foursquare](https://foursquare.com) request the limiting radius is scaled by `radiusFactor`.  
There will be data requested for the following  
`radiusFactors`: `(0.5, 0.6, 0.7, 0.8, 0.9, 1.0, 1.1, 1.2, 1.3, 1.4, 1.5)`

In [13]:
def getNearbyVenues(names, latitudes, longitudes, radii, radiusFactor):
    venues_list=[]
    for name, lat, lng, radius in zip(names, latitudes, longitudes, radii):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            FOURSQUARE_CLIENT_ID, 
            FOURSQUARE_CLIENT_SECRET, 
            VERSION, 
            round(lat,8), 
            round(lng,8), 
            round(radius*radiusFactor),
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            radiusFactor,
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Borough', 
                  'Borough_Latitude', 
                  'Borough_Longitude',
                  'radiusFactor',
                  'Venue', 
                  'Venue_Latitude', 
                  'Venue_Longitude', 
                  'Venue_Category']
    return(nearby_venues)


Save the data retrieved from [Foursquare](https://foursquare.com) in a local file:

In [14]:
fnMunichVenuesCSV = "Munich_25_Venues.csv"
radiusFactors = (0.5,0.6,0.7,0.8,0.9,1.0,1.1,1.2,1.3,1.4,1.5)

# save (cache) the data locally:
if not Path(fnMunichVenuesCSV).is_file():
    munich_venues = pd.DataFrame()
    for radiusFactor in radiusFactors:
        print("=== Retrieving venues for radiusFactor={} ===".format(radiusFactor))
        munich_venues = munich_venues.append(getNearbyVenues(names=dfMunich['Borough'],
                                             latitudes=dfMunich['coord_lat'],
                                             longitudes=dfMunich['coord_lng'],
                                             radii=dfMunich['radius(m)'],
                                             radiusFactor=radiusFactor
                                            ), ignore_index = True)
    munich_venues.to_csv(fnMunichVenuesCSV, index = False)
    print("File " + fnMunichVenuesCSV + " saved.")
else:
    print("File " + fnMunichVenuesCSV + " already exists locally.")

File Munich_25_Venues.csv already exists locally.


Load the locally stored data and take a peek:

In [15]:
munich_venues = pd.read_csv(fnMunichVenuesCSV)
print(munich_venues.shape)
print(munich_venues.dtypes)
munich_venues.head(12)

(25117, 8)
Borough               object
Borough_Latitude     float64
Borough_Longitude    float64
radiusFactor         float64
Venue                 object
Venue_Latitude       float64
Venue_Longitude      float64
Venue_Category        object
dtype: object


Borough  Borough_Latitude  Borough_Longitude  radiusFactor  \
0   Altstadt-Lehel         48.141273          11.583178           0.5   
1   Altstadt-Lehel         48.141273          11.583178           0.5   
2   Altstadt-Lehel         48.141273          11.583178           0.5   
3   Altstadt-Lehel         48.141273          11.583178           0.5   
4   Altstadt-Lehel         48.141273          11.583178           0.5   
5   Altstadt-Lehel         48.141273          11.583178           0.5   
6   Altstadt-Lehel         48.141273          11.583178           0.5   
7   Altstadt-Lehel         48.141273          11.583178           0.5   
8   Altstadt-Lehel         48.141273          11.583178           0.5   
9   Altstadt-Lehel         48.141273          11.583178           0.5   
10  Altstadt-Lehel         48.141273          11.583178           0.5   
11  Altstadt-Lehel         48.141273          11.583178           0.5   

                                Venue  Venue_Latitude  Venue_Longitude  \
0                     SEITZ Trattoria       48.141419        11.584902   
1                  Liebighof im Lehel       48.141640        11.586470   
2                           Hofgarten       48.143053        11.579955   
3   Hotel Vier Jahreszeiten Kempinski       48.138918        11.581775   
4                             Brenner       48.139555        11.580924   
5              Patisserie Café Dukatz       48.139375        11.586923   
6             Nationaltheater München       48.139599        11.579207   
7               Bayerische Staatsoper       48.139639        11.578933   
8                    The spice bazaar       48.140696        11.581910   
9                       Marstallplatz       48.140260        11.581016   
10                           Pusser's       48.138500        11.580426   
11                           Residenz       48.141284        11.579011   

              Venue_Category  
0          Trattoria/Osteria  
1          German Restaurant  
2                     Garden  
3                      Hotel  
4                 Steakhouse  
5                Pastry Shop  
6                Opera House  
7                Opera House  
8   Mediterranean Restaurant  
9                      Plaza  
10              Cocktail Bar  
11                    Palace

## Methodology <a name="methodology"></a>

The idea of this investigation is quite simple:

1) Retrieve venues for each borough using [Foursquare](https://foursquare.com)-API.  
2) Do some data wrangling to obtain the venues for each borough.  
3) Use a _k-means_ clustering algorithm and force all boroughs into two clusters: cluster one contains the _best_ boroughs.  
4) Do steps 1 to 3 for several radii around each borough's centroid, i.e. 50% to 150% of each borough's extent.  
5) For the several radii of 4) sum up all how many times a borough was classified as _best_ borough.  
6) Compare the result of 5) with the list of the website [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)

Are we able to confirm the selection of the [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) by this simple analysis?  
Are there boroughs with a similar lifestyle like the [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) but not listed?


## Analysis <a name="analysis"></a>

### Venues of each Borough

Let's start with an example to get a feeling of the data:  
Show all boroughs with the smallest `radii` by scaling each radius with the smallest `radiusFactor` and draw a blue circle accordingly.
Visualize the retrieved venues inside each _radius_.    

In [16]:
# determine a list with the smallest radii:
venues_smallestRadius = munich_venues[munich_venues['radiusFactor'] == min(radiusFactors)]

# create town map
town_map = folium.Map(location=[cMunichLat, cMunichLng], zoom_start=12)#, tiles='Mapbox Bright')

# add boroughs to map:
town_map.choropleth(
    geo_data=fnTownGeo,
    data=dfMunich,
    columns=['Borough', 'bestBorough'],
    key_on='feature.properties.FIRST_Bezi',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=1.0,
    reset=True
    )

# remove legend:
for key in town_map._children:
    if key.startswith('color_map'):
        del(town_map._children[key])
        
# town_map, add polylines to show "bestBoroughs"        
for polygon in bestBoroughsPolygons:
    folium.PolyLine(polygon, color="cyan", weight=4, opacity=1).add_to(town_map)
        
# town_map, add radii to map = rough estimation of the extent of each borough
for lat, lng, radius in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['radius(m)']):
    folium.Circle(
        [lat, lng],
        radius=radius * min(radiusFactors),
        color='blue',
        fill=False,
        parse_html=False).add_to(town_map)       

# town_map, add Venues:
for lat, lng, label in zip(venues_smallestRadius['Venue_Latitude'], venues_smallestRadius['Venue_Longitude'], venues_smallestRadius['Venue_Category']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='green',
        fill=True,
        fill_color='green',
        fill_opacity=0.5,
        parse_html=False).add_to(town_map)
    
# town_map, add markers = centroid of each borough
for lat, lng, label in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['Borough']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.4,
        parse_html=False).add_to(town_map) 
    
town_map

It is easy to see that even with a `radiusFactor` of `0.5`, there is still an overlap between the areas of influence in some boroughs.
This means that there are boroughs that are also influenced by the venues of neighboring boroughs.

In [17]:
saveMap('03', town_map)

File Munich_25_town_map_03.png already exists locally.


Show how many vanues have been found inside each _radius_, scaled by `radiusFactor` (*rFactor_x.x*): 

In [18]:
venues_count_distribution = pd.DataFrame()
for rF in radiusFactors:
    venues_count_distribution["rFactor_{:3.1f}".format(round(rF,1))] = munich_venues[munich_venues['radiusFactor'] == rF].groupby('Borough').count()['Venue']
    
venues_count_distribution

rFactor_0.5  rFactor_0.6  \
Borough                                                                        
Allach-Untermenzing                                          24           26   
Altstadt-Lehel                                              100          100   
Au-Haidhausen                                               100          100   
Aubing-Lochhausen-Langwied                                   25           30   
Berg am Laim                                                 51           62   
Bogenhausen                                                 100          100   
Feldmoching-Hasenbergl                                       24           30   
Hadern                                                       25           26   
Laim                                                         59           54   
Ludwigsvorstadt-Isarvorstadt                                100          100   
Maxvorstadt                                                 100          100   
Milbertshofen-Am Hart                                        87          100   
Moosach                                                      93          100   
Neuhausen-Nymphenburg                                       100          100   
Obergiesing-Fasangarten                                      40           46   
Pasing-Obermenzing                                           65          100   
Ramersdorf-Perlach                                           88           91   
Schwabing-Freimann                                           55           87   
Schwabing-West                                               96           45   
Schwanthalerhöhe                                             72           83   
Sendling                                                     87          100   
Sendling-Westpark                                            51           70   
Thalkirchen-Obersendling-Forstenried-Fürstenrie...           83           70   
Trudering-Riem                                               90          100   
Untergiesing-Harlaching                                      73           98   

                                                    rFactor_0.7  rFactor_0.8  \
Borough                                                                        
Allach-Untermenzing                                          31           44   
Altstadt-Lehel                                              100          100   
Au-Haidhausen                                               100          100   
Aubing-Lochhausen-Langwied                                   42           61   
Berg am Laim                                                 61           89   
Bogenhausen                                                  99          100   
Feldmoching-Hasenbergl                                       41           59   
Hadern                                                       36           39   
Laim                                                         81           96   
Ludwigsvorstadt-Isarvorstadt                                100          100   
Maxvorstadt                                                 100          100   
Milbertshofen-Am Hart                                        68           98   
Moosach                                                     100          100   
Neuhausen-Nymphenburg                                       100          100   
Obergiesing-Fasangarten                                      76           92   
Pasing-Obermenzing                                          100          100   
Ramersdorf-Perlach                                           76           92   
Schwabing-Freimann                                          100          100   
Schwabing-West                                               63           94   
Schwanthalerhöhe                                             96          100   
Sendling                                                    100          100   
Sendling-Westpark                                  

The maximum number of hits seems to be limited to 100.  
In some boroughs, the number of hits increases as the `radiusFactor` increases.  
However, there are also sporadic irregular fluctuations in the quantities. 

As an example the borough _Hadern_ has the following venue distribution for the given `radiusFactors` (*rFactor_x.x*):

In [19]:
hadern_venues = munich_venues[munich_venues['Borough'] == "Hadern"]
hadern_venues_count_distribution = pd.DataFrame()
for rF in hadern_venues['radiusFactor'].unique():
    hadern_venues_count_distribution["rFactor_{:3.1f}".format(round(rF,1))] = hadern_venues[hadern_venues['radiusFactor'] == rF].groupby('Borough').count()['Venue']
    
hadern_venues_count_distribution

rFactor_0.5  rFactor_0.6  rFactor_0.7  rFactor_0.8  rFactor_0.9  \
Borough                                                                    
Hadern            25           26           36           39           49   

         rFactor_1.0  rFactor_1.1  rFactor_1.2  rFactor_1.3  rFactor_1.4  \
Borough                                                                    
Hadern            47           66           79          100          100   

         rFactor_1.5  
Borough               
Hadern           100

Let's draw a map for the borough _Hadern_ by showing the circles of three different `radiusFactors` `(0.5, 1.0, 1.5)` and their venues inside each radius.

In [20]:
dfHadern = dfMunich[dfMunich['Borough'] == "Hadern"]

# create town map for "Hadern"
town_map = folium.Map(location=[cMunichLat, cMunichLng], zoom_start=12)#, tiles='Mapbox Bright')

# add boroughs to map:
town_map.choropleth(
    geo_data=fnTownGeo,
    data=dfMunich,
    columns=['Borough', 'bestBorough'],
    key_on='feature.properties.FIRST_Bezi',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=1.0,
    reset=True
    )

# remove legend:
for key in town_map._children:
    if key.startswith('color_map'):
        del(town_map._children[key])

# town_map, add polylines to show "bestBoroughs"        
for polygon in bestBoroughsPolygons:
    folium.PolyLine(polygon, color="cyan", weight=4, opacity=1).add_to(town_map)
        
# town_map, add radii to map = rough estimation of the extent of each borough
for radiusFactor, color in zip((0.5,1.0,1.5),('blue','red','green')):
    for lat, lng, radius in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['radius(m)']):
        folium.Circle(
            [dfHadern.iloc[0]['coord_lat'], dfHadern.iloc[0]['coord_lng']],
            radius=dfHadern.iloc[0]['radius(m)'] * radiusFactor,
            color=color,
            fill=False,
            parse_html=False).add_to(town_map)       

# town_map, add Venues:
for radiusFactor, color, size in zip((0.5,1.0,1.5),('blue','red','green'),(7,5,3)):
    for lat, lng, label in zip(hadern_venues[hadern_venues['radiusFactor']==radiusFactor]['Venue_Latitude'],  #hadern_venues['Venue_Latitude'],
                               hadern_venues[hadern_venues['radiusFactor']==radiusFactor]['Venue_Longitude'], #hadern_venues['Venue_Longitude'],
                               hadern_venues[hadern_venues['radiusFactor']==radiusFactor]['Venue_Category']   #hadern_venues['Venue_Category']
                              ):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=size,
            popup=label,
            color=color,
            weight=1,
            fill=True,
            fill_color=color,
            fill_opacity=0.3,
            parse_html=False).add_to(town_map)
    
# town_map, add markers = centroid of each borough
for lat, lng, label in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['Borough']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.4,
        parse_html=False).add_to(town_map) 
    
town_map

The map shows the _centroids_ (black dots) of each borough.
As an example for the borough of _Hadern_, the `radiusFactors` (0.5, 1.0, 1.5) are visualized accordingly by circles in three different colors (blue, red, green).
The retrieved venues of each radius are marked in the corresponding color.  
It turns out that some venues of a smaller circle are not included in the group of a larger circle.
There might be two reasons for that kind of behaviour:
* The number of results is limited to 100. It is not known which venues will be provided if more are available within a certain radius.
* [Foursquare](https://foursquare.com) _finds venues that a typical user is likely to checkin to at the provided location_, see
[API documentation](https://developer.foursquare.com/docs/api/venues/search).
Again, the selection method is unknown.  


In [21]:
saveMap('04', town_map)

File Munich_25_town_map_04.png already exists locally.


### Categories of Venues

In [22]:
print('There are {} unique categories.'.format(len(munich_venues['Venue_Category'].unique())))
print(munich_venues['Venue_Category'].unique())

There are 291 unique categories.
['Trattoria/Osteria' 'German Restaurant' 'Garden' 'Hotel' 'Steakhouse'
 'Pastry Shop' 'Opera House' 'Mediterranean Restaurant' 'Plaza'
 'Cocktail Bar' 'Palace' 'Historic Site' 'Concert Hall' 'Surf Spot'
 'Italian Restaurant' 'Theater' 'Boutique' 'Convenience Store'
 'Art Museum' 'Café' 'Snack Place' 'Restaurant' 'Vietnamese Restaurant'
 'Gourmet Shop' 'Bavarian Restaurant' 'Department Store'
 'Performing Arts Venue' 'American Restaurant' 'Pizza Place'
 'Shopping Mall' 'French Restaurant' 'Waterfall' 'Austrian Restaurant'
 'Camera Store' 'Candy Store' 'Clothing Store' 'Bar' 'Fountain' 'Wine Bar'
 'Museum' 'Monument / Landmark' 'Outdoor Sculpture' 'Beach' 'Coffee Shop'
 'Design Studio' 'Art Gallery' 'Irish Pub' 'Sporting Goods Shop' 'Church'
 'Japanese Restaurant' 'Tree' 'Greek Restaurant' 'Asian Restaurant'
 'Ice Cream Shop' 'Xinjiang Restaurant' 'Spanish Restaurant'
 'Vegetarian / Vegan Restaurant' 'Drugstore' 'Nightclub'
 'Falafel Restaurant' 'Creperie

### Most common Venues for each Borough

Do a _one hot encoding_ on the venue data:

In [23]:
munich_onehots = []
for i, rF in enumerate(radiusFactors,0):
    munich_onehots.insert(i, pd.get_dummies(munich_venues[munich_venues['radiusFactor'] == rF][['Venue_Category']], prefix="", prefix_sep="") )
    # add Borough column as first column:
    munich_onehots[i].insert(0,'Borough', munich_venues[munich_venues['radiusFactor'] == rF]['Borough'])
    print("{:2d} :  {:3.1f}  {}".format(i, rF, munich_onehots[i].shape))

 0 :  0.5  (1788, 243)
 1 :  0.6  (1918, 248)
 2 :  0.7  (2042, 247)
 3 :  0.8  (2264, 251)
 4 :  0.9  (2339, 239)
 5 :  1.0  (2360, 234)
 6 :  1.1  (2466, 231)
 7 :  1.2  (2452, 220)
 8 :  1.3  (2488, 220)
 9 :  1.4  (2500, 213)
10 :  1.5  (2500, 201)


Group the result of the _one hot encoding_ by _Borough_ using the `mean()` aggregation method and take a peek on the data of `radiusFactor=1.0`:

In [24]:
munich_groupeds = []
for i, rF in enumerate(radiusFactors,0):
    munich_groupeds.insert(i, munich_onehots[i].groupby('Borough').mean().reset_index())
    print(i, munich_groupeds[i].shape)
munich_groupeds[5]

0 (25, 243)
1 (25, 248)
2 (25, 247)
3 (25, 251)
4 (25, 239)
5 (25, 234)
6 (25, 231)
7 (25, 220)
8 (25, 220)
9 (25, 213)
10 (25, 201)


Borough  Accessories Store  \
0                                 Allach-Untermenzing               0.00   
1                                      Altstadt-Lehel               0.00   
2                                       Au-Haidhausen               0.00   
3                          Aubing-Lochhausen-Langwied               0.00   
4                                        Berg am Laim               0.01   
5                                         Bogenhausen               0.00   
6                              Feldmoching-Hasenbergl               0.00   
7                                              Hadern               0.00   
8                                                Laim               0.00   
9                        Ludwigsvorstadt-Isarvorstadt               0.00   
10                                        Maxvorstadt               0.00   
11                              Milbertshofen-Am Hart               0.00   
12                                            Moosach               0.00   
13                              Neuhausen-Nymphenburg               0.00   
14                            Obergiesing-Fasangarten               0.00   
15                                 Pasing-Obermenzing               0.00   
16                                 Ramersdorf-Perlach               0.01   
17                                 Schwabing-Freimann               0.00   
18                                     Schwabing-West               0.00   
19                                   Schwanthalerhöhe               0.00   
20                                           Sendling               0.00   
21                                  Sendling-Westpark               0.00   
22  Thalkirchen-Obersendling-Forstenried-Fürstenri...               0.00   
23                                     Trudering-Riem               0.01   
24                            Untergiesing-Harlaching               0.00   

    Afghan Restaurant  Airport  American Restaurant  Arcade  Art Gallery  \
0                0.00  0.00000             0.000000    0.00         0.00   
1                0.00  0.00000             0.010000    0.00         0.01   
2                0.01  0.00000             0.000000    0.00         0.01   
3                0.00  0.00000             0.000000    0.00         0.00   
4                0.00  0.00000             0.000000    0.00         0.00   
5                0.00  0.00000             0.000000    0.00         0.00   
6                0.00  0.01087             0.021739    0.00         0.00   
7                0.00  0.00000             0.000000    0.00         0.00   
8                0.00  0.00000             0.020000    0.00         0.00   
9                0.01  0.00000             0.000000    0.00         0.01   
10               0.00  0.00000             0.000000    0.01         0.00   
11               0.00  0.00000             0.000000    0.00         0.00   
12               0.00  0.00000             0.010000    0.00         0.00   
13               0.00  0.00000             0.000000    0.00         0.00   
14               0.00  0.00000             0.000000    0.00         0.00   
15               0.00  0.00000             0.000000    0.00         0.00   
16               0.00  0.00000             0.000000    0.00         0.00   
17               0.00  0.00000             0.000000    0.00         0.00   
18               0.01  0.00000             0.000000    0.01         0.00   
19               0.00  0.00000             0.010000    0.00         0.00   
20               0.00  0.00000             0.000000    0.00         0.00   
21               0.00  0.00000             0.000000    0.00         0.00   
22               0.00  0.00000             0.000000    0.00         0.00   
23               0.00  0.00000             0.000000    0.00         0.00   
24               0.00  0.00000             0.000000    0.00         0.00   

    Art Museum  Arts & Crafts Store  Asian Restaurant  ...  \
0         0.00                

Display the top 10 venues for each borough using `radiusFactor=1.0`.

In [25]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Borough']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))


boroughs_venues_sorted = []
for i, rF in enumerate(radiusFactors,0):
    # create a new dataframe
    boroughs_venues_sorted.insert(i, pd.DataFrame(columns=columns))
    boroughs_venues_sorted[i]['Borough'] = munich_groupeds[i]['Borough']

    for ind in np.arange(munich_groupeds[i].shape[0]):
        boroughs_venues_sorted[i].iloc[ind, 1:] = return_most_common_venues(munich_groupeds[i].iloc[ind, :], num_top_venues)

boroughs_venues_sorted[5]

Borough 1st Most Common Venue  \
0                                 Allach-Untermenzing           Supermarket   
1                                      Altstadt-Lehel                  Café   
2                                       Au-Haidhausen     German Restaurant   
3                          Aubing-Lochhausen-Langwied           Supermarket   
4                                        Berg am Laim           Supermarket   
5                                         Bogenhausen     German Restaurant   
6                              Feldmoching-Hasenbergl           Supermarket   
7                                              Hadern           Supermarket   
8                                                Laim           Supermarket   
9                        Ludwigsvorstadt-Isarvorstadt                  Café   
10                                        Maxvorstadt                  Café   
11                              Milbertshofen-Am Hart                 Hotel   
12                                            Moosach     German Restaurant   
13                              Neuhausen-Nymphenburg     German Restaurant   
14                            Obergiesing-Fasangarten      Greek Restaurant   
15                                 Pasing-Obermenzing     German Restaurant   
16                                 Ramersdorf-Perlach     German Restaurant   
17                                 Schwabing-Freimann     German Restaurant   
18                                     Schwabing-West                  Café   
19                                   Schwanthalerhöhe                 Hotel   
20                                           Sendling                  Café   
21                                  Sendling-Westpark    Italian Restaurant   
22  Thalkirchen-Obersendling-Forstenried-Fürstenri...     German Restaurant   
23                                     Trudering-Riem           Supermarket   
24                            Untergiesing-Harlaching     German Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0       German Restaurant    Italian Restaurant                 Hotel   
1                   Plaza                 Hotel          Cocktail Bar   
2                    Café          Cocktail Bar                 Plaza   
3       German Restaurant             Drugstore                Bakery   
4                   Hotel    Italian Restaurant     German Restaurant   
5      Italian Restaurant                 Hotel  Gym / Fitness Center   
6                   Hotel                Bakery             Drugstore   
7       German Restaurant                Bakery              Bus Stop   
8        Greek Restaurant             Drugstore    Italian Restaurant   
9                   Hotel     German Restaurant        Ice Cream Shop   
10                  Plaza                 Hotel            Art Museum   
11                   Café  Gym / Fitness Center      Greek Restaurant   
12     Italian Restaurant      Greek Restaurant           Beer Garden   
13     Italian Restaurant                 Hotel                  Café   
14            Supermarket     German Restaurant             Drugstore   
15            Supermarket                 Hotel             Drugstore   
16                  Hotel  Gym / Fitness Center           Supermarket   
17                 Lounge                 Hotel                Bakery   
18  Vietnamese Restaurant    Italian Restaurant            Restaurant   
19                   Café    Italian Restaurant      Asian Restaurant   
20      German Restaurant    Italian Restaurant      Greek Restaurant   
21                  Hotel                  Café        Ice Cream Shop   
22       Greek Restaurant           Zoo Exhibit  Gym / Fitness Center   
23                  Hotel     German Restaurant    Italian Restaurant   
24                   Café      Greek Restaurant           Zoo Exhibit   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                Bu

### Clustering Boroughs on Base of their Venues

Run k-means to cluster the boroughs into 2 clusters.

In [26]:
# set number of clusters
kclusters = 2

munich_grouped_clustering = []
kmeans = []
for i, rF in enumerate(radiusFactors,0):
    munich_grouped_clustering.insert(i, munich_groupeds[i].drop('Borough', 1))
    # run k-means clustering
    kmeans.insert(i, KMeans(n_clusters=kclusters, random_state=0).fit(munich_grouped_clustering[i]))
#kmeans[5].labels_ 

In [27]:
#for i, rF in enumerate(radiusFactors,0):
#    plt.hist(kmeans[i].labels_)
#    plt.show()

Merge the _Munich_ data with the cluster labels:

In [28]:
munich_merged = []
for i, rF in enumerate(radiusFactors,0):
    # add clustering labels
    if not 'Cluster_Labels' in boroughs_venues_sorted[i].columns:
        boroughs_venues_sorted[i].insert(0, 'Cluster_Labels', kmeans[i].labels_)

    munich_merged.insert(i, dfMunich)
    # merge dfMunich data with mostCommonVenue data: 
    munich_merged[i] = munich_merged[i].join(boroughs_venues_sorted[i].set_index('Borough'), on='Borough', how='inner')

#munich_merged[5]

Modify the the merged data in that kind that a _BestBorough=1_ recommendation always matches with a *Cluster_Label*=1:

In [29]:
# modify data that kind, that BestBorough=1 fits with Cluster_Labels=1 most of time
def score(a,b):
    if (a==b):
        return 1
    else:
        return 0
def swap(x):
    if (x==0):
        return 1
    else:
        return 0
    
for i, rF in enumerate(radiusFactors,0):
    munich_merged[i]['score'] = munich_merged[i].apply(lambda x: score(x['bestBorough'], x['Cluster_Labels']), axis=1)
    if (munich_merged[i]['score'].mean() < 0.5):
        munich_merged[i]['Cluster_Labels'] = munich_merged[i].apply(lambda x: swap(x['Cluster_Labels']), axis=1)
    #print(munich_merged[i]['score'].mean())
    del munich_merged[i]['score']

munich_merged[5]

Borough  Area(km**2)  Residents  \
0                                      Altstadt-Lehel         3.15      21100   
1                        Ludwigsvorstadt-Isarvorstadt         4.40      51644   
2                                         Maxvorstadt         4.30      51402   
3                                      Schwabing-West         4.36      68527   
4                                       Au-Haidhausen         4.22      61356   
5                                            Sendling         3.94      40983   
6                                   Sendling-Westpark         7.81      59643   
7                                    Schwanthalerhöhe         2.07      29743   
8                               Neuhausen-Nymphenburg        12.91      98814   
9                                             Moosach        11.09      54223   
10                              Milbertshofen-Am Hart        13.42      75094   
11                                 Schwabing-Freimann        25.67      77936   
12                                        Bogenhausen        23.71      87950   
13                                       Berg am Laim         6.31      46098   
14                                     Trudering-Riem        22.45      73206   
15                                 Ramersdorf-Perlach        19.90     116327   
16                            Obergiesing-Fasangarten         5.72      54256   
17                            Untergiesing-Harlaching         8.06      53184   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...        17.76      96714   
19                                             Hadern         9.22      49898   
20                                 Pasing-Obermenzing        16.50      74625   
21                         Aubing-Lochhausen-Langwied        34.06      47813   
22                                Allach-Untermenzing        15.45      33355   
23                             Feldmoching-Hasenbergl        28.94      61774   
24                                               Laim         5.29      56546   

    Density(resident/km**2)  Foreigners(%)  bestBorough  coord_lat  coord_lng  \
0                      6708           26.1            1  48.141273  11.583178   
1                     11734           28.4            1  48.130152  11.561218   
2                     11960           25.4            0  48.148069  11.564298   
3                     15706           22.7            1  48.166539  11.569307   
4                     14541           23.5            1  48.129727  11.594758   
5                     10405           26.9            0  48.115282  11.546057   
6                      7632           28.9            0  48.116790  11.520021   
7                     14367           33.5            0  48.136161  11.538246   
8                      7651           24.3            1  48.156452  11.519305   
9                      4888           31.5            0  48.181714  11.510923   
10                     5597           40.8            0  48.195994  11.567868   
11                     3036           29.3            1  48.192805  11.610558   
12                     3709           24.4            1  48.157458  11.643526   
13                     7300           31.9            0  48.126164  11.631715   
14                     3261           23.3            0  48.123764  11.683573   
15                     5847           33.9            0  48.099738  11.638702   
16                     9485           31.1            1  48.102744  11.593269   
17                     6601           24.1            1  48.098586  11.564134   
18                     5445           27.4            1  48.086525  11.513238   
19                     5410           27.3            0  48.113956  11.483451   
20                     4523           22.9            0  48.152697  11.463274   
21                     1404           28.4            0  48.164726  11.408340   
22                     2159           24.2            0  48.192671  11.46200

In [30]:
map_clusters = []
for i, rF in enumerate(radiusFactors,0):
    # create map
    map_clusters.insert(i, folium.Map(location=[cMunichLat, cMunichLng], zoom_start=12))

    # add boroughs to map:
    map_clusters[i].choropleth(
        geo_data=fnTownGeo,
        data=munich_merged[i],
        columns=['Borough', 'Cluster_Labels'],
        key_on='feature.properties.FIRST_Bezi',
        fill_color='YlOrRd', 
        fill_opacity=0.7, 
        line_opacity=1.0,
        #legend_name='Best Boroughs',
        reset=True
        )

    # remove legend:
    for key in map_clusters[i]._children:
        if key.startswith('color_map'):
            del(map_clusters[i]._children[key])

    # set color scheme for the clusters
    x = np.arange(kclusters)
    ys = [i + x + (i*x)**2 for i in range(kclusters)]
    colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
    rainbow = [colors.rgb2hex(i) for i in colors_array]

    # town_map, add polylines to show "bestBoroughs"
    for polygon in bestBoroughsPolygons:
        folium.PolyLine(polygon, color="cyan", weight=4, opacity=1).add_to(map_clusters[i])
        
    # town_map, add markers = centroid of each borough
    for lat, lng, label in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['Borough']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='black',
            fill=True,
            fill_color='black',
            fill_opacity=0.4,
            parse_html=False).add_to(map_clusters[i]) 

    folium.map.Marker(
        [cMunichLat+0.085,cMunichLng],
        icon=DivIcon(
            icon_size=(150,36),
            icon_anchor=(0,0),
            html='<div style="font-size: 18pt">' + "radiusFactor={:3.1f}".format(radiusFactors[i])  + '</div>',
            )
        ).add_to(map_clusters[i])


In [31]:
index=0
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=0.5 are shown as red areas:


In [32]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=0.6 are shown as red areas:


In [33]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=0.7 are shown as red areas:


In [34]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=0.8 are shown as red areas:


In [35]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=0.9 are shown as red areas:


In [36]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.0 are shown as red areas:


In [37]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.1 are shown as red areas:


In [38]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.2 are shown as red areas:


In [39]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.3 are shown as red areas:


In [40]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.4 are shown as red areas:


In [41]:
index = index + 1
print("Map of Munich's boroughs.\n" + 
      '"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.\n'+
      "By k-means clustering recommended boroughs based on radiusFactor={:3.1f} are shown as red areas:".format(radiusFactors[index]))
map_clusters[index]

Map of Munich's boroughs.
"Best Neighborhoods in Munich" (https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
By k-means clustering recommended boroughs based on radiusFactor=1.5 are shown as red areas:


Save the maps to _.html_ and _.png_ files:

In [42]:
for i, rF in enumerate(radiusFactors,0):
    print("06_{:02d}_{:03.1f}".format(i, rF).replace('.','o'))
    saveMap("06_{:02d}_{:03.1f}".format(i, rF).replace('.','o'), map_clusters[i])

06_00_0o5
File Munich_25_town_map_06_00_0o5.png already exists locally.
06_01_0o6
File Munich_25_town_map_06_01_0o6.png already exists locally.
06_02_0o7
File Munich_25_town_map_06_02_0o7.png already exists locally.
06_03_0o8
File Munich_25_town_map_06_03_0o8.png already exists locally.
06_04_0o9
File Munich_25_town_map_06_04_0o9.png already exists locally.
06_05_1o0
File Munich_25_town_map_06_05_1o0.png already exists locally.
06_06_1o1
File Munich_25_town_map_06_06_1o1.png already exists locally.
06_07_1o2
File Munich_25_town_map_06_07_1o2.png already exists locally.
06_08_1o3
File Munich_25_town_map_06_08_1o3.png already exists locally.
06_09_1o4
File Munich_25_town_map_06_09_1o4.png already exists locally.
06_10_1o5
File Munich_25_town_map_06_10_1o5.png already exists locally.


For all `radiusFactors` sum the _Cluster_Labels=1_ recommendation results from the clustering algorithm and 
compare it with the _BestBorough_ recommendations from 
[www.moving-to-munich.com](https://www.moving-to-munich.com/best-neighborhoods-in-munich/):

In [43]:
munich_ranking = pd.DataFrame(munich_merged[0]['Borough'])
munich_ranking['bestBorough'] = dfMunich['bestBorough']
munich_ranking['score'] = 0
for i, rF in enumerate(radiusFactors,0):
    for b in munich_ranking['Borough']:
        if (munich_merged[i].loc[munich_merged[i]['Borough'] == b, ['Cluster_Labels']].values[0] >0):
            munich_ranking.loc[munich_ranking['Borough'] == b, ['score']] = munich_ranking.loc[munich_ranking['Borough'] == b, ['score']] + 1
munich_ranking

Borough  bestBorough  score
0                                      Altstadt-Lehel            1     11
1                        Ludwigsvorstadt-Isarvorstadt            1     11
2                                         Maxvorstadt            0     11
3                                      Schwabing-West            1     11
4                                       Au-Haidhausen            1     11
5                                            Sendling            0     11
6                                   Sendling-Westpark            0      6
7                                    Schwanthalerhöhe            0     11
8                               Neuhausen-Nymphenburg            1     11
9                                             Moosach            0      5
10                              Milbertshofen-Am Hart            0      7
11                                 Schwabing-Freimann            1     11
12                                        Bogenhausen            1     10
13                                       Berg am Laim            0      1
14                                     Trudering-Riem            0      1
15                                 Ramersdorf-Perlach            0      4
16                            Obergiesing-Fasangarten            1      4
17                            Untergiesing-Harlaching            1     10
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...            1      4
19                                             Hadern            0      0
20                                 Pasing-Obermenzing            0      0
21                         Aubing-Lochhausen-Langwied            0      0
22                                Allach-Untermenzing            0      0
23                             Feldmoching-Hasenbergl            0      0
24                                               Laim            0      3

Add the `radiusFactors` to get some more insights...

In [44]:
munich_ranking = pd.DataFrame(munich_merged[0]['Borough'])
munich_ranking['bestBorough'] = dfMunich['bestBorough']
munich_ranking['score'] = 0
for i, rF in enumerate(radiusFactors,0):
    munich_ranking["rFactor_{:3.1f}".format(round(rF,1))] = 0
for i, rF in enumerate(radiusFactors,0):
    for b in munich_ranking['Borough']:
        if (munich_merged[i].loc[munich_merged[i]['Borough'] == b, ['Cluster_Labels']].values[0] >0):
            munich_ranking.loc[munich_ranking['Borough'] == b, ['score']] = munich_ranking.loc[munich_ranking['Borough'] == b, ['score']] + 1
        munich_ranking.loc[munich_ranking['Borough'] == b, ["rFactor_{:3.1f}".format(round(rF,1))]] =  munich_merged[i].loc[munich_merged[i]['Borough'] == b, ['Cluster_Labels']].values[0]
            
munich_ranking

Borough  bestBorough  score  \
0                                      Altstadt-Lehel            1     11   
1                        Ludwigsvorstadt-Isarvorstadt            1     11   
2                                         Maxvorstadt            0     11   
3                                      Schwabing-West            1     11   
4                                       Au-Haidhausen            1     11   
5                                            Sendling            0     11   
6                                   Sendling-Westpark            0      6   
7                                    Schwanthalerhöhe            0     11   
8                               Neuhausen-Nymphenburg            1     11   
9                                             Moosach            0      5   
10                              Milbertshofen-Am Hart            0      7   
11                                 Schwabing-Freimann            1     11   
12                                        Bogenhausen            1     10   
13                                       Berg am Laim            0      1   
14                                     Trudering-Riem            0      1   
15                                 Ramersdorf-Perlach            0      4   
16                            Obergiesing-Fasangarten            1      4   
17                            Untergiesing-Harlaching            1     10   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...            1      4   
19                                             Hadern            0      0   
20                                 Pasing-Obermenzing            0      0   
21                         Aubing-Lochhausen-Langwied            0      0   
22                                Allach-Untermenzing            0      0   
23                             Feldmoching-Hasenbergl            0      0   
24                                               Laim            0      3   

    rFactor_0.5  rFactor_0.6  rFactor_0.7  rFactor_0.8  rFactor_0.9  \
0             1            1            1            1            1   
1             1            1            1            1            1   
2             1            1            1            1            1   
3             1            1            1            1            1   
4             1            1            1            1            1   
5             1            1            1            1            1   
6             0            0            0            0            0   
7             1            1            1            1            1   
8             1            1            1            1            1   
9             0            0            0            0            1   
10            0            0            1            1            1   
11            1            1            1            1            1   
12            1            1            1            0            1   
13            0            0            0            0            0   
14            1            0            0            0            0   
15            0            0            0            0            0   
16            0            0            0            0            0   
17            1            1            1            1            0   
18            0            0            0            0            0   
19            0            0            0            0            0   
20            0            0            0            0            0   
21            0            0            0            0            0   
22            0            0            0            0            0   
23            0            0            0            0            0   
24            0            0            0            0            0   

    rFactor_1.0  rFactor_1.1  rFactor_1.2  rFactor_1.3  rFactor_1.4  \
0             1            1            1            1            1   
1             1            1            1            1

In [45]:
dfMunich = dfMunich.join(munich_ranking.drop(['bestBorough'], axis=1).set_index('Borough'), on='Borough', how='inner')
#dfMunich

A choropleth map will give a better overview: Red areas are highly recommended by the clustering algorithm.
The borders of the
[Best Neighborhoods](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
are shown as cyan polygons.   

In [46]:
# create town map
town_map = folium.Map(location=[cMunichLat, cMunichLng], zoom_start=12)#, tiles='Mapbox Bright')

# add boroughs to map:
town_map.choropleth(
    geo_data=fnTownGeo,
    data=dfMunich,
    columns=['Borough', 'score'],
    key_on='feature.properties.FIRST_Bezi',
    fill_color='YlOrRd',
    #threshold_scale=[0,1,2,3,4,5,6,7,8,9,10,11],
    fill_opacity=0.7, 
    line_opacity=1.0,
    #legend_name='Best Boroughs',
    reset=True
    )
        
# town_map, add polylines to show "bestBoroughs"
for polygon in bestBoroughsPolygons:
    folium.PolyLine(polygon, color="cyan", weight=4, opacity=1).add_to(town_map)
    
# town_map, add markers = centroid of each borough
for lat, lng, borough, score in zip(dfMunich['coord_lat'], dfMunich['coord_lng'], dfMunich['Borough'], dfMunich['score']):
    label = folium.Popup("{} - score {}".format(borough, score), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.4,
        parse_html=False).add_to(town_map) 
        
town_map        

The map shows the boroughs of Munich.
The [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are drawn as polygons with a cyan border.
The different colors of the boroughs show how often the individual borough was included in the respective cluster for the best "boroughs".
The redder the color, the more often the respective borough was selected.

In [47]:
saveMap('05', town_map)

File Munich_25_town_map_05.png already exists locally.


## Results and Discussion <a name="results"></a>

In [52]:
munich_ranking[munich_ranking['bestBorough'] == 1]

Borough  bestBorough  score  \
0                                      Altstadt-Lehel            1     11   
1                        Ludwigsvorstadt-Isarvorstadt            1     11   
3                                      Schwabing-West            1     11   
4                                       Au-Haidhausen            1     11   
8                               Neuhausen-Nymphenburg            1     11   
11                                 Schwabing-Freimann            1     11   
12                                        Bogenhausen            1     10   
16                            Obergiesing-Fasangarten            1      4   
17                            Untergiesing-Harlaching            1     10   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...            1      4   

    rFactor_0.5  rFactor_0.6  rFactor_0.7  rFactor_0.8  rFactor_0.9  \
0             1            1            1            1            1   
1             1            1            1            1            1   
3             1            1            1            1            1   
4             1            1            1            1            1   
8             1            1            1            1            1   
11            1            1            1            1            1   
12            1            1            1            0            1   
16            0            0            0            0            0   
17            1            1            1            1            0   
18            0            0            0            0            0   

    rFactor_1.0  rFactor_1.1  rFactor_1.2  rFactor_1.3  rFactor_1.4  \
0             1            1            1            1            1   
1             1            1            1            1            1   
3             1            1            1            1            1   
4             1            1            1            1            1   
8             1            1            1            1            1   
11            1            1            1            1            1   
12            1            1            1            1            1   
16            1            0            1            1            0   
17            1            1            1            1            1   
18            1            1            1            1            0   

    rFactor_1.5  
0             1  
1             1  
3             1  
4             1  
8             1  
11            1  
12            1  
16            1  
17            1  
18            0

In [53]:
munich_ranking[munich_ranking['bestBorough'] == 0]

Borough  bestBorough  score  rFactor_0.5  rFactor_0.6  \
2                  Maxvorstadt            0     11            1            1   
5                     Sendling            0     11            1            1   
6            Sendling-Westpark            0      6            0            0   
7             Schwanthalerhöhe            0     11            1            1   
9                      Moosach            0      5            0            0   
10       Milbertshofen-Am Hart            0      7            0            0   
13                Berg am Laim            0      1            0            0   
14              Trudering-Riem            0      1            1            0   
15          Ramersdorf-Perlach            0      4            0            0   
19                      Hadern            0      0            0            0   
20          Pasing-Obermenzing            0      0            0            0   
21  Aubing-Lochhausen-Langwied            0      0            0            0   
22         Allach-Untermenzing            0      0            0            0   
23      Feldmoching-Hasenbergl            0      0            0            0   
24                        Laim            0      3            0            0   

    rFactor_0.7  rFactor_0.8  rFactor_0.9  rFactor_1.0  rFactor_1.1  \
2             1            1            1            1            1   
5             1            1            1            1            1   
6             0            0            0            1            1   
7             1            1            1            1            1   
9             0            0            1            1            1   
10            1            1            1            1            1   
13            0            0            0            0            0   
14            0            0            0            0            0   
15            0            0            0            1            1   
19            0            0            0            0            0   
20            0            0            0            0            0   
21            0            0            0            0            0   
22            0            0            0            0            0   
23            0            0            0            0            0   
24            0            0            0            0            0   

    rFactor_1.2  rFactor_1.3  rFactor_1.4  rFactor_1.5  
2             1            1            1            1  
5             1            1            1            1  
6             1            1            1            1  
7             1            1            1            1  
9             1            1            0            0  
10            1            1            0            0  
13            0            1            0            0  
14            0            0            0            0  
15            1            1            0            0  
19            0            0            0            0  
20            0            0            0            0  
21            0            0            0            0  
22            0            0            0            0  
23            0            0            0            0  
24            0            1            1            1

In [48]:
munich_ranking[munich_ranking['score'] == 11]

Borough  bestBorough  score  rFactor_0.5  \
0                 Altstadt-Lehel            1     11            1   
1   Ludwigsvorstadt-Isarvorstadt            1     11            1   
2                    Maxvorstadt            0     11            1   
3                 Schwabing-West            1     11            1   
4                  Au-Haidhausen            1     11            1   
5                       Sendling            0     11            1   
7               Schwanthalerhöhe            0     11            1   
8          Neuhausen-Nymphenburg            1     11            1   
11            Schwabing-Freimann            1     11            1   

    rFactor_0.6  rFactor_0.7  rFactor_0.8  rFactor_0.9  rFactor_1.0  \
0             1            1            1            1            1   
1             1            1            1            1            1   
2             1            1            1            1            1   
3             1            1            1            1            1   
4             1            1            1            1            1   
5             1            1            1            1            1   
7             1            1            1            1            1   
8             1            1            1            1            1   
11            1            1            1            1            1   

    rFactor_1.1  rFactor_1.2  rFactor_1.3  rFactor_1.4  rFactor_1.5  
0             1            1            1            1            1  
1             1            1            1            1            1  
2             1            1            1            1            1  
3             1            1            1            1            1  
4             1            1            1            1            1  
5             1            1            1            1            1  
7             1            1            1            1            1  
8             1            1            1            1            1  
11            1            1            1            1            1

In [49]:
munich_ranking[munich_ranking['score'] == 10]

Borough  bestBorough  score  rFactor_0.5  rFactor_0.6  \
12              Bogenhausen            1     10            1            1   
17  Untergiesing-Harlaching            1     10            1            1   

    rFactor_0.7  rFactor_0.8  rFactor_0.9  rFactor_1.0  rFactor_1.1  \
12            1            0            1            1            1   
17            1            1            0            1            1   

    rFactor_1.2  rFactor_1.3  rFactor_1.4  rFactor_1.5  
12            1            1            1            1  
17            1            1            1            1

In [50]:
munich_ranking[(munich_ranking['score'] == 4) & (munich_ranking['bestBorough'] == 1)]

Borough  bestBorough  score  \
16                            Obergiesing-Fasangarten            1      4   
18  Thalkirchen-Obersendling-Forstenried-Fürstenri...            1      4   

    rFactor_0.5  rFactor_0.6  rFactor_0.7  rFactor_0.8  rFactor_0.9  \
16            0            0            0            0            0   
18            0            0            0            0            0   

    rFactor_1.0  rFactor_1.1  rFactor_1.2  rFactor_1.3  rFactor_1.4  \
16            1            0            1            1            0   
18            1            1            1            1            0   

    rFactor_1.5  
16            1  
18            0

In [51]:
munich_ranking[(munich_ranking['score'] == 11) & (munich_ranking['bestBorough'] == 0)]

Borough  bestBorough  score  rFactor_0.5  rFactor_0.6  \
2       Maxvorstadt            0     11            1            1   
5          Sendling            0     11            1            1   
7  Schwanthalerhöhe            0     11            1            1   

   rFactor_0.7  rFactor_0.8  rFactor_0.9  rFactor_1.0  rFactor_1.1  \
2            1            1            1            1            1   
5            1            1            1            1            1   
7            1            1            1            1            1   

   rFactor_1.2  rFactor_1.3  rFactor_1.4  rFactor_1.5  
2            1            1            1            1  
5            1            1            1            1  
7            1            1            1            1

The map and the tables above show:

* Most of the [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) are also recommended correctly by the clustering algorithm with the highest score of 11.
* Two of the [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) show almost a maximum score of 10.
* Two other boroughs from the list of [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/) were only able to achieve a score of 4 and are therefore not highly recommended by the clustering algorithm.
* There are three boroughs that are not on the list of the [Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/), but which are recommended by the clustering algorithm with the highest score of 11. 

In summary, the list of the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
from the website
[www.moving-to-munich.com](https://www.moving-to-munich.com)
can be confirmed very well with the help of the _k-means_ clustering algorithm.  
The clustering algorithm gives an indication of which boroughs should be considered in a more differentiated way.  
It also recommends three boroughs that are not on the original list of the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/).


The following reservations can be expressed about the above analyses:

* The website
[www.moving-to-munich.com](https://www.moving-to-munich.com)
presents a list of the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/).
Some of the neighborhoods mentioned are only sub-districts of the official list of districts.
This affects the exact comparability.
* The venue data retrieved by
[Foursquare](https://foursquare.com)
is affected by the
[API](https://developer.foursquare.com/docs/api/venues/search)
behaviour:
The number of results is limited to 100. It is not known which venues will be provided if more are available within a certain radius.
Furthermore [Foursquare](https://foursquare.com)
_finds venues that a typical user is likely to checkin to at the provided location, at the current moment in time_, i.e. the exact selection method is unknown and depends on the time of the request.
* The method of clustering into two groups is quite simple.
In order to obtain more confidence in the result, further statistical methods should be applied:
How well are the individual boroughs comparable with each other?
Do other data such as crime rates, house prices, rents, social composition of the population show similar relationships?

Last but not least:  
By having a look at the map it is noticeable that 
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
are located at or close to the Isar river.
Perhaps this is the feature that makes the boroughs particularly interesting.

## Conclusion <a name="conclusion"></a>

The selection of the
[Best Neighborhoods in Munich](https://www.moving-to-munich.com/best-neighborhoods-in-munich/)
was confirmed by the venue information provided by
[Foursquare](https://foursquare.com) requests.  
In addition, the clustering algorithm used found further boroughs that may have similar characteristics.
These would also be worth a look if you are planning to move to Munich.

Due to the simplicity of the clustering algorithm used, the question could be raised whether the analysis was successful by accident.  
Therefore, this project ends with the recommendation to conduct an in-depth investigation on the basis of further data not yet considered.
